# Test wind forecast with barometric pressure

In [9]:
# install the modules on the OS
#!pip install influxdb
#!pip3 install ipynb

# import the modules
import pandas as pd
import datetime as dt
import numpy as np
import influxdb
import os
import math
import scipy.stats as st
import plotly.graph_objects as go

from ipynb.fs.full.config_and_functions import *

In [10]:
def plot_corr_pressure_wind():
    
    client = influxdb.DataFrameClient(DB_HOST, DB_PORT, DB_USER, DB_PASSWORD, DB_NAME)

    query = """SELECT
                mean(wind_force_avg_10min) AS mean_wind_force_avg_10min,
                mean(barometric_pressure_qfe) AS mean_barometric_pressure_qfe,
                mean(wind_direction) AS mean_wind_direction,
                mean(air_temperature) AS mean_air_temperature
                FROM "meteorology"."autogen"."{}"
                WHERE time < now()
                GROUP BY time(1d) fill(previous)""".format(station_name)

    df = pd.DataFrame(client.query(query)[station_name])
    
    # remove outliers
    df = remove_outliers(df, "mean_barometric_pressure_qfe")
    df = remove_outliers(df, "mean_wind_force_avg_10min")
    
    x = df.index
    
    # y0 = barometric pressure
    y0 = df["mean_barometric_pressure_qfe"]

    # y1 = wind force
    y1 = df["mean_wind_force_avg_10min"]

    # y2 = wind direction
    y2 = df["mean_wind_direction"]
    df.loc[df.mean_wind_direction > 360, 'mean_wind_direction'] = df.mean_wind_direction % 360

    # y3 = air temperature
    y3 = df["mean_air_temperature"]
    

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=x, y=y0,
                        mode='lines',
                        name='barometric pressure', 
                        marker=dict(color="rgb(255,67,67)")))
    fig.add_trace(go.Scatter(x=x, y=y1,
                        mode='lines',
                        name='wind force', 
                        marker=dict(color="rgb(67,255,67)")))
    fig.add_trace(go.Scatter(x=x, y=y2,
                        mode='lines',
                        name='wind direction', 
                        marker=dict(color="rgb(67,100,67)")))
    fig.add_trace(go.Scatter(x=x, y=y3,
                        mode='lines',
                        name='air temperature', 
                        marker=dict(color="rgb(100,150,67)")))
    fig.update_layout(barmode='stack')
    fig.show()
    
    
    # Normalize data
    y0_normalized = ((y0-y0.mean()) / (y0.max() - y0.min()))
    y1_normalized = (y1-y1.mean()) / (y1.max() - y1.min())
    y2_normalized = (y2-y2.mean()) / (y2.max() - y2.min())
    y3_normalized = (y3-y3.mean()) / (y3.max() - y3.min())
    fig_normalized = go.Figure()

    fig_normalized.add_trace(go.Scatter(x=x, y=y0_normalized,
                        mode='lines',
                        name='barometric pressure', 
                        marker=dict(color="rgb(255,67,67)")))
    fig_normalized.add_trace(go.Scatter(x=x, y=y1_normalized,
                        mode='lines',
                        name='wind force', 
                        marker=dict(color="rgb(67,255,67)")))
    fig_normalized.add_trace(go.Scatter(x=x, y=y2_normalized,
                        mode='lines',
                        name='wind direction', 
                        marker=dict(color="rgb(67,100,67)")))
    fig_normalized.add_trace(go.Scatter(x=x, y=y3_normalized,
                        mode='lines',
                        name='air temperature', 
                        marker=dict(color="rgb(100,150,67)")))
    fig_normalized.update_layout(barmode='stack')
    fig_normalized.show()


# call function
plot_corr_pressure_wind()

In [11]:
def get_barometric_pressure_in_current_time_period():
    
    query = """SELECT 
                mean(barometric_pressure_qfe) AS mean_barometric_pressure_qfe
                FROM "meteorology"."autogen"."{}"
                WHERE time > now() - 6h GROUP BY time(1h) fill(previous)""".format(station_name)

    df = pd.DataFrame(client.query(query)[station_name])
    
    message = """Der in den letzten 6 Stunden {} Luftdruck,
                der {},
                geht einher mit {} Windstärke.
                In den kommenden 6 Stunden wird die Windstärke zwischen {} und {} Beaufort liegen."""
    
    barometric_pressure_value_last = float(df.iloc[-1:].values[0])
    barometric_pressure_value_6h_ago = float(df.iloc[0:].values[0])
    
    if (barometric_pressure_value_last < barometric_pressure_value_6h_ago):
        string = "gesunkene"
        string2 = "zunehmender"
    elif (barometric_pressure_value_last == barometric_pressure_value_6h_ago):
        string = "gleich gebliebene"
        string2 = "gleich bleibender"
    else:
        string = "gestiegene"
        string2 = "abnehmender"
        
    message = message.format(string, "{}", "{}", "{}", "{}")

    # Get data for pressure distribution/quantiles
    query = """SELECT 
                mean(barometric_pressure_qfe) AS mean_barometric_pressure_qfe
                FROM "meteorology"."autogen"."{}"
                WHERE time < now() GROUP BY time(5d)""".format(station_name)

    df = pd.DataFrame(client.query(query)[station_name])
    
    df = remove_outliers(df, "mean_barometric_pressure_qfe") # Filter outliers and replace them with median
    df_filtered = get_data_in_current_time_period(df, 15, 15) # Filter for current time period
    
    if (barometric_pressure_value_last < df_filtered.quantile(0.2).values):
        string = "unterdurchschnittlich tief"
    elif (barometric_pressure_value_last < df_filtered.quantile(0.5).values):
        string = "leicht unterdurchschnittlich tief"
    elif (barometric_pressure_value_last < df_filtered.quantile(0.8).values):
        string = "leicht überdurchschnittlich hoch"
    else:
        string = "überdurchschnittlich hoch"
    string += " ist"
        
    message = message.format(string, "{}", "{}", "{}")
    message = message.format(string2, "{}", "{}")
    
    # Get data for wind force prediction
    query = """SELECT
            last(wind_force_avg_10min) AS last_wind_force_avg_10min,
            last(barometric_pressure_qfe) AS last_barometric_pressure_qfe
            FROM "meteorology"."autogen"."{}" """.format(station_name)

    df_last = pd.DataFrame(client.query(query)[station_name])
    last_barometric_pressure_qfe = float(df_last["last_barometric_pressure_qfe"].values)
    last_wind_force_avg_10min = float(df_last["last_wind_force_avg_10min"].values)

    # find similar conditions, stop if something found
    # "simulate" HAVING clause
    len_of_df = 0
    factor = 0.1
    while len_of_df <= 0:
        
        query = """SELECT
                (wind_force_avg_10min),
                (barometric_pressure_qfe)
                FROM "meteorology"."autogen"."{}"
                WHERE
                    (barometric_pressure_qfe > {} AND barometric_pressure_qfe < {})
                    AND
                    (wind_force_avg_10min > {} AND wind_force_avg_10min < {})
                    AND
                    (time < now() - 1d)""".format(
                            station_name,
                            last_barometric_pressure_qfe - factor * 2,
                            last_barometric_pressure_qfe + factor * 2,
                            last_wind_force_avg_10min - (factor * 1),
                            last_wind_force_avg_10min + (factor * 1))

        df = pd.DataFrame(client.query(query)[station_name])
        len_of_df = len(df)
        factor += 0.1
        if factor == 10:
            break

    # loop in widening day span, break if 20 results are found
    days_span = 10
    df_f = df
    len_of_df_f = len(df_f)
        
    while len_of_df_f > 20:
        
        df_f = get_data_in_current_time_period(df, days_span, days_span) # Filter for current time period

        len_of_df_f = len(df_f)
        days_span -= 1
        if days_span == 1:
            break

    # take first result and use for forecast
    df_final = df.loc[
        df_f.iloc[0:].index[0] + dt.timedelta(hours=-2)
        : 
        df_f.iloc[0:].index[0] + dt.timedelta(hours=6)
    ]
    
    # go 2 hours back and 6 forward, get min and max values
    datetime_start = (df_f.iloc[0:].index[0] + dt.timedelta(hours=-2)).tz_localize(tz = None) 
    datetime_end = (df_f.iloc[0:].index[0] + dt.timedelta(hours=6)).tz_localize(tz = None) 

    query = """SELECT
                (wind_force_avg_10min),
                (barometric_pressure_qfe)
                FROM "meteorology"."autogen"."{}"
                WHERE
                    (time >= '{}' AND time <= '{}')""".format(
                        station_name,
                        datetime_start,
                        datetime_end
    )
    
    df_final = pd.DataFrame(client.query(query)[station_name])

    message = message.format(
        round_up(df_final["wind_force_avg_10min"].quantile(0.2), 1),
        round_up(df_final["wind_force_avg_10min"].quantile(0.8), 1))
    
    return message

get_barometric_pressure_in_current_time_period()

'Der in den letzten 6 Stunden gesunkene Luftdruck,\n                der überdurchschnittlich hoch ist,\n                geht einher mit zunehmender Windstärke.\n                In den kommenden 6 Stunden wird die Windstärke zwischen 1.6 und 3.0 Beaufort liegen.'